<a href="https://colab.research.google.com/github/AubinGil/BERT_classifier/blob/main/BERT_attention_mechanism_visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Step 1: Imports
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from bertviz import head_view

# Step 2: Set CPU
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")


# Step 3: Load tokenizer from saved directory
tokenizer = AutoTokenizer.from_pretrained("/content/drive/MyDrive/logs")

# Step 4: Reconstruct model + load fine-tuned weights
model = AutoModelForSequenceClassification.from_pretrained(
    "Simonlee711/Clinical_ModernBERT", output_attentions=True
)

# Load the state dictionary and adjust keys if necessary
state_dict = torch.load("/content/drive/MyDrive/logs/model.pt", map_location=device)
new_state_dict = {}
for k, v in state_dict.items():
    if k.startswith('_orig_mod.'):
        new_state_dict[k[len('_orig_mod.'):]] = v
    # Attempt to map classifier keys
    elif k == 'classifier.0.weight':
        new_state_dict['classifier.weight'] = v
    elif k == 'classifier.0.bias':
        new_state_dict['classifier.bias'] = v
    elif k == 'classifier.3.weight' or k == 'classifier.3.bias':
        # Ignore these keys as they don't seem to map to the expected classifier
        pass
    else:
        new_state_dict[k] = v

model.load_state_dict(new_state_dict, strict=False)
model.to(device)
model.eval()

# Step 5: Prepare text
text = "Her diarrhea has resolved. Her appetite is improved. She reports bilateral lower extremity edema for about 1 week"

# Step 6: Tokenize and prepare inputs
inputs = tokenizer(text, return_tensors="pt", truncation=True, max_length=512)
inputs = {k: v.to(device) for k, v in inputs.items()}

# Step 7: Run model to get attention
with torch.no_grad():
    outputs = model(**inputs, output_attentions=True)

attentions = outputs.attentions
tokens = tokenizer.convert_ids_to_tokens(inputs["input_ids"][0])

# Step 8: Visualize attention
head_view(attentions, tokens)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at Simonlee711/Clinical_ModernBERT and are newly initialized: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


<IPython.core.display.Javascript object>